In [48]:
import panel as pn
import pandas as pd
import yfinance as yf
from datetime import datetime
import plotly.graph_objects as go
from plotly.offline import init_notebook_mode
import requests
import copy
import cufflinks as cf
import warnings
from bokeh.models.widgets.tables import BooleanFormatter
import matplotlib.pyplot as plt
from matplotlib.figure import Figure
import seaborn as sns
import numpy as np
import scipy.stats as scs
import statsmodels.api as sm
import statsmodels.tsa.api as smt


plt.style.use("dark_background")

warnings.filterwarnings("ignore")

cf.go_offline()
init_notebook_mode()

pn.extension("plotly", "tabulator", "ipywidgets", sizing_mode="stretch_width")

TEMPLATE = "plotly_dark"
TICKER_DEFAULT = "MSFT"
# set the default start date to 1 year ago
START_DATE_DEFAULT = (datetime.now() - pd.DateOffset(years=1)).strftime("%Y-%m-%d")

In [47]:
stocks = sorted(
    [
        "MSFT",  # Microsoft
        "GOOGL",  # Google
        "META",  # Meta
        "TSLA",  # Tesla
        "AAPL",  # Apple
        "AMZN",  # Amazon
        "NFLX",  # Netflix
        "NVDA",  # Nvidia
        "AMD",  # AMD
        "INTC",  # Intel
        "CSCO",  # Cisco
        "QCOM",  # Qualcomm
        "ADBE",  # Adobe
        "PYPL",  # PayPal
        "CRM",  # Salesforce
        "ORCL",  # Oracle
        "IBM",  # IBM
        "TXN",  # Texas Instruments
        "MU",  # Micron
        "AVGO",  # Broadcom
        "INTU",  # Intuit
        "NOW",  # ServiceNow
        "UBER",  # Uber
        "SNAP",  # Snap
        "LYFT",  # Lyft
        "ZM",  # Zoom
        "WORK",  # Slack
        "PINS",  # Pinterest
        "SPOT",  # Spotify
        "SQ",  # Square
        "SHOP",  # Shopify
        "ROKU",  # Roku
        "DOCU",  # DocuSign
        "OKTA",  # Okta
        "ZS",  # Zscaler
        "CRWD",  # CrowdStrike
        "MDB",  # MongoDB
        "DDOG",  # Datadog
        "NET",  # Cloudflare
        "ESTC",  # Elastic
        "PANW",  # Palo Alto Networks
        "VMW",  # VMware
        "SPLK",  # Splunk
        "WDAY",  # Workday
        "TEAM",  # Atlassian
        "COUP",  # Coupa
        "AYX",  # Alteryx
        "ZEN",  # Zendesk
        "HUBS",  # Hubspot
        "DT",  # Dynatrace
        "ZI",  # ZoomInfo
        "FSLY",  # Fastly
        "TWLO",  # Twilio
    ]
)

In [49]:
@pn.cache(ttl=600)
def get_historical_data(
    ticker=TICKER_DEFAULT,
    start_date=START_DATE_DEFAULT,
    end_date=datetime.now().strftime("%Y-%m-%d"),
):
    """
    Downloads the historical data from Yahoo Finance and caches it.

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    start_date : str
        The start date for the historical data
    end_date : str
        The end date for the historical data
    """

    df = yf.download(
        ticker, start=start_date, end=end_date, progress=False, auto_adjust=True
    )
    return df


def get_candlestick_chart(
    ticker=TICKER_DEFAULT,
    start_date=START_DATE_DEFAULT,
    end_date=datetime.now().strftime("%Y-%m-%d"),
):
    """
    Returns a candlestick chart

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    start_date : str
        The start date for the historical data
    end_date : str
        The end date for the historical data
    """
    df = get_historical_data(ticker, start_date, end_date)
    fig = go.Figure(
        data=[
            go.Candlestick(
                x=df.index,
                open=df["Open"],
                high=df["High"],
                low=df["Low"],
                close=df["Close"],
                name="Candlestick",
            )
        ]
    )
    fig.update_layout(
        template=TEMPLATE,
        title="Candlestick Chart",
        xaxis_title="Date",
        yaxis_title="Price",
    )
    return fig


def get_line_chart(
    ticker="MSFT", start_date="2020-01-01", end_date=datetime.now().strftime("%Y-%m-%d")
):
    """
    Returns a line chart

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    start_date : str
        The start date for the historical data
    end_date : str
        The end date for the historical data
    """
    df = get_historical_data(ticker, start_date, end_date)
    fig = go.Figure(
        data=[
            go.Scatter(
                x=df.index,
                y=df["Close"],
                name="Close",
            )
        ]
    )
    fig.update_layout(
        title="Line Chart", xaxis_title="Date", yaxis_title="Price", template=TEMPLATE
    )
    return fig


def download_company_logo(ticker: str = TICKER_DEFAULT):
    """
    Download a company's logo based on its ticker symbol.

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    # URL format for logo images from a stock market website
    url = f"https://storage.googleapis.com/iex/api/logos/{ticker}.png"

    try:
        response = requests.get(url)
        # Check if the response is successful (status code 200)
        if response.status_code == 200:
            return response.content
        else:
            return f"Failed to download logo. Status code: {response.status_code}"
    except Exception as e:
        return str(e)


def get_close_price_info(ticker: str = TICKER_DEFAULT):
    """
    Create a Panel with the company logo and the last close price.

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    # get the last close price and last close date
    last_close_price, last_close_date = get_ticker_last_close_price(ticker)

    # Download the logo for Microsoft (MSFT)
    logo_content = download_company_logo(ticker)

    # Create a Panel image from the logo bytes
    logo = pn.panel(logo_content, width=100, height=100, align="center")

    # Create a Panel indicator for the close price

    close_price = pn.indicators.Number(
        name=f"Close Price (USD, {last_close_date.strftime('%Y-%m-%d')})",
        value=299,
        format=f"$ {last_close_price:.2f}",
        colors=[(33, "green"), (66, "gold"), (100, "red")],
    )
    return pn.Row(logo, close_price)


def get_ticker_last_close_price(ticker: str = TICKER_DEFAULT):
    """
    Get the last close price and last close date for a ticker.

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    df = get_historical_data(ticker)
    last_close_price = df["Close"].iloc[-1]
    last_close_date = df.index[-1]
    return last_close_price, last_close_date


@pn.cache()
def get_ticker_info(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker info

    Parameters
    ----------
     ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_info = ticker.info

    return ticker_info


def get_business_summary(ticker: str = TICKER_DEFAULT):
    """
    Create panel with business summary

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    business_summary = ticker.info["longBusinessSummary"]

    return pn.pane.Markdown(f"## Business Summary\n{business_summary}")


def get_company_officers(ticker: str = TICKER_DEFAULT):
    """
    Create panel with company officers

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    info = copy.deepcopy(get_ticker_info(ticker))

    company_officers = info["companyOfficers"]

    # format yearBorn values to be integers
    for officer in company_officers:
        if "yearBorn" in officer.keys():
            officer["yearBorn"] = f"{int(officer['yearBorn']):.0f}"
        if "fiscalYear" in officer.keys():
            officer["fiscalYear"] = f"{int(officer['fiscalYear']):.0f}"
        if "totalPay" in officer.keys():
            officer["totalPay"] = f"{float(officer['totalPay']):.2f}"
        if "age" in officer.keys():
            officer["age"] = f"{float(officer['age']):.0f}"

    # remove unneeded keys
    for officer in company_officers:
        del officer["maxAge"]
        del officer["exercisedValue"]
        del officer["unexercisedValue"]

    company_officers = pd.DataFrame(company_officers)
    company_officers = company_officers.reset_index(drop=True)

    # reorder columns
    company_officers = company_officers[
        [
            "name",
            "title",
            "yearBorn",
            "age",
            "totalPay",
            "fiscalYear",
        ]
    ]

    company_officers = (
        company_officers.style.set_properties(
            **{"text-align": "left"}, subset=["name", "title"]
        )
        .set_properties(**{"text-align": "center"}, subset=["yearBorn", "age"])
        .set_properties(**{"text-align": "right"}, subset=["totalPay", "fiscalYear"])
        .format({"totalPay": "{:.2f}"})
        .format({"yearBorn": "{:.0f}"})
        .format({"age": "{:.0f}"})
        .format({"fiscalYear": "{:.0f}"})
    )

    return pn.widgets.Tabulator(company_officers, show_index=False)


def get_options_chain(ticker: str = TICKER_DEFAULT):
    """
    Create panel with options chain

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    ticker = yf.Ticker(ticker)
    options_chain = ticker.option_chain()

    # format values of percentChange column to be percentages with 2 decimal places
    options_chain.calls["percentChange"] = options_chain.calls["percentChange"].map(
        "{:.2f}%".format
    )

    # format values of impliedVolatility column to be percentages with 2 decimal places
    options_chain.calls["impliedVolatility"] = options_chain.calls[
        "impliedVolatility"
    ].map("{:.2f}%".format)

    bokeh_formatters = {
        "bool": BooleanFormatter(),
    }

    return pn.widgets.Tabulator(
        options_chain.calls, show_index=False, formatters=bokeh_formatters
    )


def get_balance_sheet(ticker: str = TICKER_DEFAULT):
    """
    Create panel with balance sheet

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    ticker = yf.Ticker(ticker)
    balance_sheet = ticker.balance_sheet

    # format columns to be dates
    balance_sheet.columns = pd.to_datetime(balance_sheet.columns).date

    balance_sheet = balance_sheet.reset_index()

    # rename index column to metric
    balance_sheet.rename(columns={"index": "Metric"}, inplace=True)

    # format index to be left aligned
    balance_sheet = balance_sheet.style.set_properties(
        **{"text-align": "left"}, subset=["Metric"]
    )
    return pn.widgets.Tabulator(balance_sheet, show_index=False)


def get_cashflow(ticker: str = TICKER_DEFAULT):
    """
    Create panel with cashflow

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    ticker = yf.Ticker(ticker)
    cashflow = ticker.cashflow

    # format columns to be dates
    cashflow.columns = pd.to_datetime(cashflow.columns).date

    cashflow = cashflow.reset_index()

    # rename index column to metric
    cashflow.rename(columns={"index": "Metric"}, inplace=True)

    # format index to be left aligned
    cashflow = cashflow.style.set_properties(
        **{"text-align": "left"}, subset=["Metric"]
    )
    return pn.widgets.Tabulator(cashflow, show_index=False)


def get_income_statement(ticker: str = TICKER_DEFAULT):
    """
    Create panel with income statement

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    ticker = yf.Ticker(ticker)
    income_statement = ticker.financials

    # format columns to be dates
    income_statement.columns = pd.to_datetime(income_statement.columns).date

    income_statement = income_statement.reset_index()

    # rename index column to metric
    income_statement.rename(columns={"index": "Metric"}, inplace=True)

    # format index to be left aligned
    income_statement = income_statement.style.set_properties(
        **{"text-align": "left"}, subset=["Metric"]
    )
    return pn.widgets.Tabulator(income_statement, show_index=False)
    """
    Create panel with statistics

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    ticker = yf.Ticker(ticker)
    statistics = pd.DataFrame(ticker.info)

    # remove unneeded keys
    del statistics["companyOfficers"]
    del statistics["zip"]
    del statistics["phone"]
    del statistics["longBusinessSummary"]
    del statistics["city"]
    del statistics["state"]
    del statistics["country"]
    del statistics["website"]
    del statistics["address1"]
    del statistics["industry"]
    del statistics["sector"]
    del statistics["fullTimeEmployees"]
    del statistics["maxAge"]

    # format values of marketCap to be integers
    statistics["marketCap"] = f"{int(statistics['marketCap']):.0f}"

    # format values of enterpriseValue to be integers
    statistics["enterpriseValue"] = f"{int(statistics['enterpriseValue']):.0f}"

    # format values of trailingPE to be integers
    statistics["trailingPE"] = f"{float(statistics['trailingPE']):.2f}"

    # format values of forwardPE to be integers
    statistics["forwardPE"] = f"{float(statistics['forwardPE']):.2f}"

    # format values of profitMargins to be integers
    statistics["profitMargins"] = f"{float(statistics['profitMargins']):.2f}"

    # format values of floatShares to be integers
    statistics["floatShares"] = f"{int(statistics['floatShares']):.0f}"

    # format values of sharesOutstanding to be integers
    statistics["sharesOutstanding"] = f"{int(statistics['sharesOutstanding']):.0f}"

    # format values of sharesShort to be integers
    statistics["sharesShort"] = f"{int(statistics['sharesShort']):.0f}"

    # format values of sharesShortPriorMonth to be integers
    statistics[
        "sharesShortPriorMonth"
    ] = f"{int(statistics['sharesShortPriorMonth']):.0f}"

    # format values of heldPercentInsiders to be integers
    statistics[
        "heldPercentInsiders"
    ] = f"{float(statistics['heldPercentInsiders']):.2f}"

    # format values of heldPercentInstitutions to be integers
    statistics[
        "heldPercentInstitutions"
    ] = f"{float(statistics['heldPercentInstitutions']):.2f}"

    # format values of shortRatio to be integers
    statistics["shortRatio"] = f"{float(statistics['shortRatio']):.2f}"

    # format values of shortPercentOfFloat to be integers
    statistics[
        "shortPercentOfFloat"
    ] = f"{float(statistics['shortPercentOfFloat']):.2f}"

    # format values of beta to be integers
    statistics["beta"] = f"{float(statistics['beta']):.2f}"

    # format values of trailingEps to be integers
    statistics["trailingEps"] = f"{float(statistics['trailingEps']):.2f}"

    # format values of forwardEps to be integers
    statistics["forwardEps"] = f"{float(statistics['forwardEps']):.2f}"

    # format values of bookValue to be integers
    statistics["bookValue"] = f"{float(statistics['bookValue']):.2f}"

    # format values of priceToBook to be integers
    statistics["priceToBook"] = f"{float(statistics['priceToBook']):.2f}"

    # format values of enterpriseToRevenue to be integers
    statistics[
        "enterpriseToRevenue"
    ] = f"{float(statistics['enterpriseToRevenue']):.2f}"

    # format values of enterpriseToEbitda to be integers
    statistics["enterpriseToEbitda"] = f"{float(statistics['enterpriseToEbitda']):.2f}"

    return pn.widgets.Tabulator(pd.DataFrame(statistics), show_index=True)


def get_ticker_holders(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker holders

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_holders = ticker.major_holders.reset_index()

    # rename index column to holder
    ticker_holders.rename(columns={"index": "Holder"}, inplace=True)

    # format values of Value column to be percentages with 2 decimal places except for the last row
    ticker_holders["Value"][:-1] = ticker_holders["Value"][:-1].map("{:.2%}".format)

    return pn.widgets.Tabulator(ticker_holders, show_index=False)


def get_ticker_mutual_fund_holders(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker mutual fund holders

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)

    ticker_mutualfund_holders = ticker.mutualfund_holders.reset_index()

    # rearrange columns
    ticker_mutualfund_holders = ticker_mutualfund_holders[
        ["Holder", "Date Reported", "Shares", "Value", "pctHeld"]
    ]

    # format values of pctHeld to be percentages with 2 decimal places
    ticker_mutualfund_holders["pctHeld"] = ticker_mutualfund_holders["pctHeld"].map(
        "{:.2%}".format
    )

    # format values of date reported to be dates
    ticker_mutualfund_holders["Date Reported"] = pd.to_datetime(
        ticker_mutualfund_holders["Date Reported"]
    ).dt.date

    return pn.widgets.Tabulator(ticker_mutualfund_holders, show_index=False)


def get_ticker_recommendations(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker recommendations

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_recommendations = ticker.recommendations

    return pn.widgets.Tabulator(ticker_recommendations, show_index=False)


def get_ticker_calendar(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker calendar

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_calendar = ticker.calendar

    return pn.widgets.Tabulator(pd.DataFrame(ticker_calendar), show_index=False)


def get_ticker_actions(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker actions

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_actions = ticker.actions

    # format index as date strings
    ticker_actions.index = ticker_actions.index.strftime("%Y-%m-%d")

    # foramt values of split column to be integers
    ticker_actions["Stock Splits"] = ticker_actions["Stock Splits"].map("{:.0f}".format)

    return pn.widgets.Tabulator(ticker_actions)


def get_ticker_splits(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker splits

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_splits = ticker.splits

    return pn.widgets.Tabulator(ticker_splits, show_index=False)


def get_ticker_sustainability(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker sustainability

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_sustainability = ticker.sustainability

    return pn.widgets.Tabulator(ticker_sustainability, show_index=False)


def get_ticker_earnings(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker earnings

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_earnings = ticker.earnings

    return pn.widgets.Tabulator(ticker_earnings, show_index=False)


def get_ticker_quarterly_earnings(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker quarterly earnings

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_quarterly_earnings = ticker.quarterly_earnings

    return pn.widgets.Tabulator(ticker_quarterly_earnings, show_index=False)


def get_ticker_dividends(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker dividends

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    ticker_dividends = ticker.dividends

    return pn.widgets.Tabulator(pd.DataFrame(ticker_dividends), show_index=False)


def get_instiutional_holders(ticker: str = TICKER_DEFAULT):
    """
    Create panel with ticker quarterly earnings

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """
    ticker = yf.Ticker(ticker)
    instiutional_holders = ticker.institutional_holders

    # rearrange columns
    instiutional_holders = instiutional_holders[
        ["Holder", "Date Reported", "Shares", "Value", "pctHeld"]
    ]

    # format values of pctHeld to be percentages with 2 decimal places
    instiutional_holders["pctHeld"] = instiutional_holders["pctHeld"].map(
        "{:.2%}".format
    )

    # format values of date reported to be dates
    instiutional_holders["Date Reported"] = pd.to_datetime(
        instiutional_holders["Date Reported"]
    ).dt.date

    # format values of holder column to be left aligned
    instiutional_holders = instiutional_holders.style.set_properties(
        **{"text-align": "left"}, subset=["Holder"]
    )

    return pn.widgets.Tabulator(instiutional_holders, show_index=False)


def get_bollinger_bands_chart(
    ticker: str = "MSFT",
    start_date: str = "2020-01-01",
    end_date: str = datetime.now().strftime("%Y-%m-%d"),
    bb_n: int = 20,
    bb_k: int = 2,
):
    """Returns a Bollinger Bands chart"""
    df = get_historical_data(ticker, start_date, end_date)

    qf = cf.QuantFig(
        df,
        title=f"TA Dashboard - {ticker}",
        legend="right",
        name=f"{ticker}",
        showlegend=True,
        width=1000,
    )

    qf.add_bollinger_bands(periods=bb_n, boll_std=bb_k)

    return qf.iplot(asFigure=True, theme="henanigans")


def get_macd_chart(
    ticker: str = "MSFT",
    start_date: str = "2020-01-01",
    end_date: str = datetime.now().strftime("%Y-%m-%d"),
    macd_fast: int = 12,
    macd_slow: int = 26,
    macd_signal: int = 9,
):
    """Returns a MACD chart"""
    df = get_historical_data(ticker, start_date, end_date)

    qf = cf.QuantFig(
        df,
        title=f"MACD - {ticker}",
        legend="right",
        name=f"{ticker}",
        showlegend=True,
        width=1000,
    )

    qf.add_macd(fast_period=macd_fast, slow_period=macd_slow, signal_period=macd_signal)

    return qf.iplot(asFigure=True, theme="henanigans")


def get_rsi_chart(
    ticker: str = "MSFT",
    start_date: str = "2020-01-01",
    end_date: str = datetime.now().strftime("%Y-%m-%d"),
    rsi_periods: int = 14,
    rsi_upper: int = 70,
    rsi_lower: int = 30,
):
    """Returns a RSI chart"""
    df = get_historical_data(ticker, start_date, end_date)

    qf = cf.QuantFig(
        df,
        title=f"RSI - {ticker}",
        legend="right",
        name=f"{ticker}",
        showlegend=True,
        width=1000,
    )

    qf.add_rsi(
        periods=rsi_periods, rsi_upper=rsi_upper, rsi_lower=rsi_lower, showbands=True
    )

    return qf.iplot(asFigure=True, theme="henanigans")


def detect_outliers(
    ticker: str = TICKER_DEFAULT, rolling_window: int = 21, n_sigmas: int = 3
):
    """
    Outlier detection using rolling statistics

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    df = get_historical_data(ticker)
    df["rtn"] = df["Close"].pct_change()
    df = df[["rtn"]].copy()
    df_rolling = df.rolling(window=rolling_window).agg(["mean", "std"])
    df_rolling.columns = df_rolling.columns.droplevel()
    df = df.join(df_rolling)
    df["upper"] = df["mean"] + n_sigmas * df["std"]
    df["lower"] = df["mean"] - n_sigmas * df["std"]
    df["outlier"] = df.apply(
        lambda x: x["rtn"] > x["upper"] or x["rtn"] < x["lower"], axis=1
    )

    # plot returns and threshold with markers for outliers
    fig, ax = plt.subplots()

    df[["rtn", "upper", "lower"]].plot(ax=ax)
    ax.scatter(
        df.loc[df["outlier"]].index,
        df.loc[df["outlier"], "rtn"],
        color="red",
        label="outlier",
    )
    ax.set_title(f"{ticker}'s stock returns")
    ax.legend(loc="center left", bbox_to_anchor=(1, 0.5))

    sns.despine()
    plt.tight_layout()

    return pn.pane.Matplotlib(fig, sizing_mode="stretch_width", fixed_aspect=False)


def plot_returns_distribution(df):
    """
    Plot returns distribution

    Parameters
    ----------
    df : DataFrame
        DataFrame with returns
    """
    r_range = np.linspace(min(df["log_rtn"]), max(df["log_rtn"]), num=1000)
    mu = df["log_rtn"].mean()
    sigma = df["log_rtn"].std()
    norm_pdf = scs.norm.pdf(r_range, loc=mu, scale=sigma)

    fig = Figure(figsize=(12, 4))
    ax = fig.subplots(1, 2)

    # histogram
    sns.distplot(df.log_rtn, kde=False, norm_hist=True, ax=ax[0])
    ax[0].set_title(f"Distribution of returns", fontsize=16)
    ax[0].plot(r_range, norm_pdf, "g", lw=2, label=f"N({mu:.2f}, {sigma**2:.4f})")
    ax[0].legend(loc="upper left")

    # Q-Q plot
    qq = sm.qqplot(df.log_rtn.values, line="s", ax=ax[1])
    ax[1].set_title("Q-Q plot", fontsize=16)

    sns.despine()
    plt.tight_layout()

    return pn.pane.Matplotlib(fig, sizing_mode="stretch_width", fixed_aspect=False)


def plot_volatility_clustering(df):
    """
    Plot volatility clustering

    Parameters
    ----------
    df : DataFrame
        DataFrame with returns
    """

    # create new figure
    fig, ax = plt.subplots(1, 1, figsize=(12, 4))

    df["log_rtn"].plot(title="Daily returns", ax=ax)

    sns.despine()
    plt.tight_layout()

    return pn.pane.Matplotlib(fig, sizing_mode="stretch_width", fixed_aspect=False)


def get_descriptive_stats_table(df):
    """
    Get descriptive statistics table

    Parameters
    ----------
    df : DataFrame
        DataFrame with returns
    """

    jb_test = scs.jarque_bera(df["log_rtn"].values)

    stats = {
        "Range of dates": f"{min(df.index.date)} - {max(df.index.date)}",
        "Number of observations": df.shape[0],
        "Mean": f"{df.log_rtn.mean():.4f}",
        "Median": f"{df.log_rtn.median():.4f}",
        "Min": f"{df.log_rtn.min():.4f}",
        "Max": f"{df.log_rtn.max():.4f}",
        "Std deviation": f"{df.log_rtn.std():.4f}",
        "Skewness": f"{df.log_rtn.skew():.4f}",
        "Kurtosis": f"{df.log_rtn.kurtosis():.4f}",
        "Jarque-Bera statistic": f"{jb_test[0]:.2f} with p-value: {jb_test[1]:.2f}",
    }

    # create table
    stats_df = pd.DataFrame.from_dict(stats, orient="index", columns=["Value"])

    # format table
    stats_df = stats_df.style.set_properties(
        **{"text-align": "center"}, subset=["Value"]
    )

    return pn.widgets.Tabulator(stats_df, show_index=True)


def plot_abscense_of_autocorrelation(df):
    """
    Plot absence of autocorrelation

    Parameters
    ----------
    df : DataFrame
        DataFrame with returns
    """

    N_LAGS = 50
    SIGNIFICANCE_LEVEL = 0.05

    # create new figure
    fig, ax = plt.subplots(1, 1, figsize=(12, 4))

    acf = smt.graphics.plot_acf(
        df["log_rtn"], lags=N_LAGS, alpha=SIGNIFICANCE_LEVEL, ax=ax
    )

    sns.despine()
    plt.tight_layout()

    return pn.pane.Matplotlib(fig, sizing_mode="stretch_width", fixed_aspect=False)


def plot_small_and_decreasing_autocorrelations(df):
    """
    Plot small and decreasing autocorrelations

    Parameters
    ----------
    df : DataFrame
        DataFrame with returns
    """

    fig, ax = plt.subplots(2, 1, figsize=(12, 6))
    SIGNIFICANCE_LEVEL = 0.05
    N_LAGS = 50

    smt.graphics.plot_acf(
        df["log_rtn"] ** 2, lags=N_LAGS, alpha=SIGNIFICANCE_LEVEL, ax=ax[0]
    )
    ax[0].set(title="Autocorrelation Plots", ylabel="Squared Returns")

    smt.graphics.plot_acf(
        np.abs(df["log_rtn"]), lags=N_LAGS, alpha=SIGNIFICANCE_LEVEL, ax=ax[1]
    )
    ax[1].set(ylabel="Absolute Returns", xlabel="Lag")

    sns.despine()
    plt.tight_layout()

    return pn.pane.Matplotlib(fig, sizing_mode="stretch_width", fixed_aspect=False)


def plot_leverage_effect(df):
    """
    Plot leverage effect

    Parameters
    ----------
    df : DataFrame
        DataFrame with returns
    """

    df["rolling_std_252"] = df[["log_rtn"]].rolling(window=252).std()
    df["rolling_std_21"] = df[["log_rtn"]].rolling(window=21).std()

    fig, ax = plt.subplots(3, 1, sharex=True, figsize=(12, 9))

    df["Close"].plot(ax=ax[0])
    ax[0].set(title="Price time series", ylabel="Price ($)")

    df["log_rtn"].plot(ax=ax[1])
    ax[1].set(ylabel="Log returns")

    df["rolling_std_252"].plot(ax=ax[2], color="r", label="Rolling Volatility 252d")
    df["rolling_std_21"].plot(ax=ax[2], color="g", label="Rolling Volatility 21d")
    ax[2].set(ylabel="Moving Volatility", xlabel="Date")
    ax[2].legend()

    sns.despine()
    plt.tight_layout()

    return pn.pane.Matplotlib(fig, sizing_mode="stretch_width", fixed_aspect=False)


def get_stylized_facts_charts(ticker: str = TICKER_DEFAULT):
    """
    Create panel with stylized facts charts. The stylized facts are:
    1. Non-Gaussian distribution of returns
    2. Volatility clustering
    3. Absence of autocorrelation
    4. Small and decreasing autocorrelations of squared and absolute returns
    5. Leverage effect

    Parameters
    ----------
    ticker : str
        The ticker symbol for the company
    """

    df = get_historical_data(ticker)
    df["log_rtn"] = np.log(df["Close"] / df["Close"].shift(1))
    df = df[["Close", "log_rtn"]].dropna()

    # Non-Gaussian distribution of returns
    fig1 = plot_returns_distribution(df)
    fig2 = get_descriptive_stats_table(df)

    # Volatility clustering
    fig3 = plot_volatility_clustering(df)

    # Absence of autocorrelation
    fig4 = plot_abscense_of_autocorrelation(df)

    # Small and decreasing autocorrelations of squared and absolute returns
    fig5 = plot_small_and_decreasing_autocorrelations(df)

    # Leverage effect
    fig6 = plot_leverage_effect(df)

    return pn.Column(
        pn.pane.Markdown("## 1. Non-Gaussian distribution of returns"),
        fig1,
        pn.pane.Markdown("### Descriptive statistics"),
        fig2,
        pn.pane.Markdown("## 2. Volatility clustering"),
        fig3,
        pn.pane.Markdown("## 3. Absence of autocorrelation"),
        fig4,
        pn.pane.Markdown(
            "## 4. Small and decreasing autocorrelations of squared and absolute returns"
        ),
        fig5,
        pn.pane.Markdown("## 5. Leverage effect"),
        fig6,
    )

In [71]:
asset_selector = pn.widgets.Select(name="Asset", options=stocks, value="MSFT")

start_date_selector = pn.widgets.DatePicker(
    name="Start Date", value=pd.to_datetime("2023-01-01").date()
)

end_date_selector = pn.widgets.DatePicker(
    name="End Date", value=pd.to_datetime("today").date()
)

main_box = pn.WidgetBox(
    "### Main Parameters",
    asset_selector,
    start_date_selector,
    end_date_selector,
)

n_param = pn.widgets.IntSlider(name="N", value=20, start=1, end=40, step=1)
k_param = pn.widgets.FloatSlider(name="k", value=2, start=0.5, end=4, step=0.5)

bollinger_box = pn.WidgetBox("### Bollinger Bands", n_param, k_param, width=400)

macd_fast = pn.widgets.IntSlider(
    name="Fast Moving Average:", value=12, start=2, end=50, step=1, width=200
)

macd_slow = pn.widgets.IntSlider(
    name="Slow Moving Average:", value=26, start=2, end=50, step=1
)

macd_signal = pn.widgets.IntSlider(
    name="Signal Line:", value=9, start=2, end=50, step=1
)

macd_box = pn.WidgetBox("### MACD", macd_fast, macd_slow, macd_signal, width=400)

rsi_periods = pn.widgets.IntSlider(name="Periods", value=14, start=2, end=50, step=1)

rsi_upper = pn.widgets.IntSlider(
    name="Upper Threshold", value=70, start=1, end=100, step=1
)

rsi_lower = pn.widgets.IntSlider(
    name="Lower Threshold", value=30, start=1, end=100, step=1
)

rsi_box = pn.WidgetBox("### RSI", rsi_periods, rsi_upper, rsi_lower, width=400)

indicator_box = pn.WidgetBox(
    "### Indicator Parameters", bollinger_box, macd_box, rsi_box
)

param_box = pn.Column(main_box, indicator_box)

bound_line_chart = pn.bind(
    get_line_chart,
    ticker=asset_selector,
    start_date=start_date_selector,
    end_date=end_date_selector,
)

bound_candlestick_chart = pn.bind(
    get_candlestick_chart,
    ticker=asset_selector,
    start_date=start_date_selector,
    end_date=end_date_selector,
)

bound_bollinger_bands_chart = pn.bind(
    get_bollinger_bands_chart,
    ticker=asset_selector,
    start_date=start_date_selector,
    end_date=end_date_selector,
    bb_n=n_param,
    bb_k=k_param,
)

bound_macd_chart = pn.bind(
    get_macd_chart,
    ticker=asset_selector,
    start_date=start_date_selector,
    end_date=end_date_selector,
    macd_fast=macd_fast,
    macd_slow=macd_slow,
    macd_signal=macd_signal,
)

bound_rsi_chart = pn.bind(
    get_rsi_chart,
    ticker=asset_selector,
    start_date=start_date_selector,
    end_date=end_date_selector,
    rsi_periods=rsi_periods,
    rsi_upper=rsi_upper,
    rsi_lower=rsi_lower,
)

charts = pn.Column(
    bound_candlestick_chart,
    bound_bollinger_bands_chart,
    bound_macd_chart,
    bound_rsi_chart,
    width=800,
)


rolling_window_slider = pn.widgets.IntSlider(
    name="Rolling Window", value=21, start=1, end=40, step=1
)
n_sigmas_slider = pn.widgets.FloatSlider(
    name="N of Sigmas", value=3, start=0.5, end=4, step=0.5
)

detect_outliers_box = pn.WidgetBox(
    "### Outlier Detection Using Rolling Stats",
    rolling_window_slider,
    n_sigmas_slider,
    width=400,
)

bound_outlier_detection = pn.bind(
    detect_outliers,
    ticker=asset_selector,
    rolling_window=rolling_window_slider,
    n_sigmas=n_sigmas_slider,
)

bound_stylized_facts_charts = pn.bind(
    get_stylized_facts_charts,
    ticker=asset_selector,
)

dashboard = pn.Row(param_box, charts, width=1400)

price_row = pn.bind(get_close_price_info, ticker=asset_selector)

In [41]:
tabs = pn.Tabs(
    (
        "Overview",
        pn.Column(
            price_row,
            pn.pane.Markdown("## Summary Detail"),
            pn.bind(get_business_summary, ticker=asset_selector),
            pn.pane.Markdown("## Company Officers"),
            pn.bind(get_company_officers, ticker=asset_selector),
            pn.pane.Markdown("## Holders"),
            pn.bind(get_ticker_holders, ticker=asset_selector),
            pn.pane.Markdown("## Institutional Holders"),
            pn.bind(get_instiutional_holders, ticker=asset_selector),
            pn.pane.Markdown("## Mutual Fund Holders"),
            pn.bind(get_ticker_mutual_fund_holders, ticker=asset_selector),
            bound_candlestick_chart,
        ),
    ),
    (
        "Financials",
        pn.Column(
            pn.pane.Markdown("## Financials"),
            pn.Tabs(
                (
                    "Income Statement",
                    pn.Column(
                        pn.pane.Markdown("## Income Statement"),
                        pn.bind(get_income_statement, ticker=asset_selector),
                    ),
                ),
                (
                    "Cashflow",
                    pn.Column(
                        pn.pane.Markdown("## Cashflow"),
                        pn.bind(get_cashflow, ticker=asset_selector),
                    ),
                ),
                (
                    "Balance Sheet",
                    pn.Column(
                        pn.pane.Markdown("## Balance Sheet"),
                        pn.bind(get_balance_sheet, ticker=asset_selector),
                    ),
                ),
            ),
            pn.pane.Markdown("## Calendar"),
            pn.bind(get_ticker_calendar, ticker=asset_selector),
            pn.pane.Markdown("## Recommendations"),
            pn.bind(get_ticker_recommendations, ticker=asset_selector),
            pn.pane.Markdown("## Actions"),
            pn.bind(get_ticker_actions, ticker=asset_selector),
        ),
    ),
    (
        "Technicals",
        pn.Column(
            pn.Row(bollinger_box, bound_bollinger_bands_chart),
            pn.Row(macd_box, bound_macd_chart),
            pn.Row(rsi_box, bound_rsi_chart),
        ),
    ),
    (
        "Options",
        pn.Column(
            pn.pane.Markdown("## Options Chain"),
            pn.bind(get_options_chain, ticker=asset_selector),
        ),
    ),
    ("Sustainability", pn.pane.Alert("Coming soon...", alert_type="warning")),
    (
        "Outliers",
        pn.Column(
            pn.Row(detect_outliers_box, bound_outlier_detection),
        ),
    ),
    (
        "Stylized Facts",
        bound_stylized_facts_charts,
    ),
)

NameError: name 'price_row' is not defined

In [73]:
# Define the template
ACCENT = "#BB2649"

template = pn.template.FastGridTemplate(
    title="Stock Analysis Dashboard - standa",
    accent_base_color=ACCENT,
    header_background=ACCENT,
    prevent_collision=True,
    save_layout=True,
    theme_toggle=False,
    theme="dark",
    row_height=160,
    favicon="standa.ico",
)

In [76]:
template.main[0:3, 0:3] = main_box
template.main[0:3, 3:12] = bound_line_chart
template.main[3:12, :] = tabs

In [75]:
template.servable()

FastGridTemplate
    [js_area] HTML(None, height=0, margin=0, sizing_mode='fixed', width=0)
    [actions] TemplateActions()
    [browser_info] BrowserInfo()
    [busy_indicator] LoadingSpinner(height=20, width=20)
    [main-11325653984] ParamFunction(function, _pane=Plotly, defer_load=False, sizing_mode='stretch_width')
    [main-11377809488] ParamFunction(function, _pane=Plotly, defer_load=False, sizing_mode='stretch_width')
    [main-11409973392] Column(sizing_mode='stretch_width')
        [0] WidgetBox(sizing_mode='stretch_width')
            [0] Markdown(str, sizing_mode='stretch_width')
            [1] Select(name='Asset', options=['MSFT', 'GOOGL', ...], sizing_mode='stretch_width', value='MSFT')
            [2] DatePicker(name='Start Date', sizing_mode='stretch_width', value=datetime.date(2020, 1, 1))
            [3] DatePicker(name='End Date', sizing_mode='stretch_width', value=datetime.date(2024, ...)
        [1] WidgetBox(sizing_mode='stretch_width')
            [0] Markdown(str, sizing_mode='stretch_width')
            [1] WidgetBox(sizing_mode='stretch_width')
                [0] Markdown(str, sizing_mode='stretch_width')
                [1] IntSlider(end=40, name='N', sizing_mode='stretch_width', start=1, value=20)
                [2] FloatSlider(end=4, name='k', sizing_mode='stretch_width', start=0.5, step=0.5, value=2)
            [2] WidgetBox(sizing_mode='stretch_width')
                [0] Markdown(str, sizing_mode='stretch_width')
                [1] IntSlider(end=50, name='Fast Moving Average:', sizing_mode='stretch_width', start=2, value=12)
                [2] IntSlider(end=50, name='Slow Moving Average:', sizing_mode='stretch_width', start=2, value=26)
                [3] IntSlider(end=50, name='Signal Line:', sizing_mode='stretch_width', start=2, value=9)
            [3] WidgetBox(sizing_mode='stretch_width')
                [0] Markdown(str, sizing_mode='stretch_width')
                [1] IntSlider(end=50, name='Periods', sizing_mode='stretch_width', start=2, value=14)
                [2] IntSlider(end=100, name='Upper Threshold', sizing_mode='stretch_width', start=1, value=70)
                [3] IntSlider(end=100, name='Lower Threshold', sizing_mode='stretch_width', start=1, value=30)